<a href="https://colab.research.google.com/github/cfong32/key-sentence-extraction/blob/main/exp12_dataset_results.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Step 1. Install and load necessary packages

In [ ]:
# install necessary programs 
!pip install -q datasets rouge_score
!pip install tqdm
!pip install -q datasets rouge_score sentence-transformers

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 468.7/468.7 kB 17.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 200.1/200.1 kB 11.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 132.9/132.9 kB 6.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.5/110.5 kB 4.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.2/212.2 kB 8.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 114.2/114.2 kB 980.3 kB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 158.8/158.8 kB 7.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 264.6/264.6 kB 11.3 MB/s eta 0:00:00
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.0/86.0 kB 8.1 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━

In [ ]:
# import packages
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from tqdm.auto import tqdm
from datasets import load_dataset
from spacy.lang.en import English
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.metrics import precision_score, recall_score, f1_score
from rouge_score.rouge_scorer import RougeScorer
from sentence_transformers import SentenceTransformer 
from itertools import cycle
from functools import partial
from textwrap import wrap
from IPython.display import HTML as html_print

# Step 2. Define variables

In [ ]:
# Defining options and values:
pd.set_option('display.min_rows', 4)
tqdm.pandas()
tqdm = partial(tqdm, position=0, leave=True)

# Define BERT model
sbert = SentenceTransformer('all-MiniLM-L6-v2')

# Step 3. Define all functions for this project

In [ ]:
# function that splits articles into sentences
# input: "df" = dataframe of interest, "column" = column containing the paragraphs
# output: data frame with "sentences"
def tokenizer(df):
  spacy_eng_nlp = English()
  spacy_eng_nlp.add_pipe("sentencizer")

  df['sentences'] = df.progress_apply(
    lambda x: (
      [str(s) for s in spacy_eng_nlp(x.article).sents]
    ),
  axis=1
  )
  return df

In [ ]:
# calculate TF-IDF (Term Frequency-Inverse Document Frequency)
# then calculate the cosine-similarity of each sentence to the "article"
# every entry of df['tfidf_cossim'] will be an ndarray indicating cossim of the sentences
def TFIDF_sim(df):
  articles = df.article.tolist()
  tfidf = TfidfVectorizer().fit(articles)

  df['TFIDF_sim'] = df.progress_apply(
    lambda x: (
      cosine_similarity(
        tfidf.transform([x.article]),
        tfidf.transform(x.sentences)
        )[0]
    ),
    axis=1
  )
  return df

In [ ]:
def SBERT_sim(df):
  # Define model
  sbert = SentenceTransformer('all-MiniLM-L6-v2')

  # Embeddings:
  df['sbert_embeddings'] = df.progress_apply(
    lambda x: sbert.encode(x.sentences + [x.article, x.highlights]),
    axis=1
  )

  df['SBERT_s2a_sim'] = df.progress_apply(
    lambda x: (
        cosine_similarity(
            x.sbert_embeddings[[-2]],   # x.article encoded
            x.sbert_embeddings[:-2]     # x.sentences encoded
        )[0]
    ),
    axis=1
  )

  df['SBERT_s2h_sim'] = df.progress_apply(
    lambda x: (
        cosine_similarity(
            x.sbert_embeddings[[-1]],   # x.highlights encoded
            x.sbert_embeddings[:-2]     # x.sentences encoded
        )[0]
    ),
    axis=1
  )
  df = df.drop(columns='sbert_embeddings')
  return df

In [ ]:
def rouge_score(df):
  rouge = RougeScorer(['rouge1', 'rouge2', 'rougeL'])

  df['raw_ROUGE'] = df.progress_apply(
    lambda x: (
      [rouge.score(x.highlights, sentence)
      for sentence in x.sentences]
    ),
    axis=1
  )
  df['R1'] = df.raw_ROUGE.map(lambda xs: np.array([x['rouge1'].fmeasure for x in xs]))
  df['R2'] = df.raw_ROUGE.map(lambda xs: np.array([x['rouge2'].fmeasure for x in xs]))
  df['RL'] = df.raw_ROUGE.map(lambda xs: np.array([x['rougeL'].fmeasure for x in xs]))
  df['ROUGE_mean'] = (df['R1'] + df['R2'] + df['RL']) / 3
  return df

In [ ]:
def cal_ranking(x):
    return np.argsort(np.argsort(x)) / (len(x)-1)
def ranks(df):
  df['rank_by_TFIDF']     = df.TFIDF_sim    .map(cal_ranking)
  df['rank_by_ROUGE']     = df.ROUGE_mean   .map(cal_ranking)
  df['rank_by_SBERT_s2a'] = df.SBERT_s2a_sim.map(cal_ranking)
  df['rank_by_SBERT_s2h'] = df.SBERT_s2h_sim.map(cal_ranking)
  return df

In [ ]:
from sklearn.metrics import f1_score
from tqdm.auto import tqdm

def cal_topKpctF1(true_rank_by, pred_rank_by, K):
    true = true_rank_by >= (1-K/100)
    pred = pred_rank_by >= (1-K/100)
    return f1_score(true, pred)

def append_topKpct_f1(df, K, true_rank_by, pred_rank_by, outp_prefix):
    df[f'{outp_prefix}_top{K}%_f1'] = df.progress_apply(
        lambda x: cal_topKpctF1(x[true_rank_by], x[pred_rank_by], K),
        axis=1
    )

def compute_topKpct_f1_scores(df):
    Ks = [1, 5, 10, 20, 40, 60, 80, 100]
    for K in Ks:
        # predict by TFIDF, validate by ROUGE
        append_topKpct_f1(df, K,
                          true_rank_by='rank_by_ROUGE',
                          pred_rank_by='rank_by_TFIDF',
                          outp_prefix='TFIDF_ROUGE')

        # predict by SBERT, validate by ROUGE
        append_topKpct_f1(df, K,
                          true_rank_by='rank_by_ROUGE',
                          pred_rank_by='rank_by_SBERT_s2a',
                          outp_prefix='SBERT_ROUGE')

        # predict by TFIDF, validate by SBERT (sentence-to-highlights)
        append_topKpct_f1(df, K,
                          true_rank_by='rank_by_SBERT_s2h',
                          pred_rank_by='rank_by_TFIDF',
                          outp_prefix='TFIDF_SBERT')

        # predict by SBERT (sentence-to-article), validate by SBERT (sentence-to-highlights)
        append_topKpct_f1(df, K,
                          true_rank_by='rank_by_SBERT_s2h',
                          pred_rank_by='rank_by_SBERT_s2a',
                          outp_prefix='SBERT_SBERT')
    return df

# Step 4. Process Datasets

In [ ]:
import locale
locale.getpreferredencoding = lambda: "UTF-8"
!pip install py7zr

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 66.3/66.3 kB 8.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 93.0/93.0 kB 14.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 390.4/390.4 kB 36.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 138.7/138.7 kB 18.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.6/49.6 kB 6.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 357.2/357.2 kB 26.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 91.1 MB/s eta 0:00:00


In [ ]:
# Load dataset into a dataframe
#cnn_dailymail_dataset = load_dataset('cnn_dailymail', '3.0.0', split = 'test')
SAMsum_dataset = load_dataset('samsum', split = 'test')

Generating train split:   0%|          | 0/14732 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/819 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/818 [00:00<?, ? examples/s]

Dataset samsum downloaded and prepared to /root/.cache/huggingface/datasets/samsum/samsum/0.0.0/f1d7c6b7353e6de335d444e424dc002ef70d1277109031327bc9cc6af5d3d46e. Subsequent calls will reuse this data.


In [ ]:
#cnn_dailymail_df = pd.DataFrame({"article": cnn_dailymail_dataset['article'],"highlights": cnn_dailymail_dataset['highlights']})
#cnn_dailymail_df = tokenizer(cnn_dailymail_df)
#cnn_dailymail_df = TFIDF_sim(cnn_dailymail_df)
#cnn_dailymail_df = rouge_score(cnn_dailymail_df)
#cnn_dailymail_df = SBERT_sim(cnn_dailymail_df)
#cnn_dailymail_df = ranks(cnn_dailymail_df)
#cnn_dailymail_df = compute_topKpct_f1_scores(cnn_dailymail_df)

In [ ]:
#cnn_dailymail_df

In [ ]:
SAMsum_df = pd.DataFrame({"article": SAMsum_dataset['dialogue'],"highlights": SAMsum_dataset['summary']})
SAMsum_df = tokenizer(SAMsum_df)
SAMsum_df = TFIDF_sim(SAMsum_df)
SAMsum_df = rouge_score(SAMsum_df)
SAMsum_df = SBERT_sim(SAMsum_df)
SAMsum_df = ranks(SAMsum_df)
SAMsum_df = compute_topKpct_f1_scores(SAMsum_df)

  0%|          | 0/819 [00:00<?, ?it/s]

  0%|          | 0/819 [00:00<?, ?it/s]

  0%|          | 0/819 [00:00<?, ?it/s]

  0%|          | 0/819 [00:00<?, ?it/s]

  0%|          | 0/819 [00:00<?, ?it/s]

...

/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_classification.py:1609: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, "true nor predicted", "F-score is", len(true_sum))
/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_classification.py:1609: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, "true nor predicted", "F-score is", len(true_sum))
/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_classification.py:1609: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, "true nor predicted", "F-score is", len(true_sum))
/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_cl

  0%|          | 0/819 [00:00<?, ?it/s]

/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_classification.py:1609: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, "true nor predicted", "F-score is", len(true_sum))
/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_classification.py:1609: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, "true nor predicted", "F-score is", len(true_sum))
/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_classification.py:1609: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, "true nor predicted", "F-score is", len(true_sum))
/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_cl

  0%|          | 0/819 [00:00<?, ?it/s]

/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_classification.py:1609: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, "true nor predicted", "F-score is", len(true_sum))
/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_classification.py:1609: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, "true nor predicted", "F-score is", len(true_sum))
/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_classification.py:1609: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, "true nor predicted", "F-score is", len(true_sum))
/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_cl

In [ ]:
SAMsum_df

article  \
0    Hannah: Hey, do you have Betty's number?\nAman...   
1    Eric: MACHINE!\r\nRob: That's so gr8!\r\nEric:...   
..                                                 ...   
817  Cora: Have you heard how much fuss British med...   
818  Rachel: <file_other>\r\nRachel: Top 50 Best Fi...   

                                            highlights  \
0    Hannah needs Betty's number but Amanda doesn't...   
1    Eric and Rob are going to watch a stand-up on ...   
..                                                 ...   
817  There was a meet-and-greet with James Charles ...   
818  Rachel sends a list of Top 50 films of 2018. J...   

                                             sentences  \
0    [Hannah: Hey, do you have Betty's number?, \nA...   
1    [Eric: MACHINE!, \r\nRob: That's so gr8!, \r\n...   
..                                                 ...   
817  [Cora: Have you heard how much fuss British me...   
818  [Rachel: <file_other>\r\nRachel: Top 50 Best F...   

                                             TFIDF_sim  \
0    [0.4707139621865806, 0.7425290655024488, 0.972...   
1    [0.6616773495281106, 0.48311666648993845, 0.58...   
..                                                 ...   
817  [0.5908163640290298, 0.3593888893159542, 0.045...   
818  [0.7309913895707748, 0.5441862682783769, 0.844...   

                                             raw_ROUGE  \
0    [{'rouge1': (0.625, 0.3125, 0.4166666666666667...   
1    [{'rouge1': (0.5, 0.08333333333333333, 0.14285...   
..                                                 ...   
817  [{'rouge1': (0.42105263157894735, 0.5333333333...   
818  [{'rouge1': (0.44, 0.5238095238095238, 0.47826...   

                                                    R1  \
0    [0.4166666666666667, 0.28571428571428575, 0.13...   
1    [0.14285714285714285, 0.11764705882352941, 0.1...   
..                                                 ...   
817  [0.47058823529411764, 0.0, 0.0, 0.585365853658...   
818  [0.4782608695652174, 0.08, 0.16666666666666666...   

                                                    R2  \
0                      [0.18181818181818182, 0.0, 0.0]   
1    [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.117...   
..                                                 ...   
817  [0.43750000000000006, 0.0, 0.0, 0.512820512820...   
818  [0.22727272727272727, 0.0, 0.04347826086956521...   

                                                    RL  \
0    [0.3333333333333333, 0.28571428571428575, 0.08...   
1    [0.14285714285714285, 0.11764705882352941, 0.1...   
..                                                 ...   
817  [0.47058823529411764, 0.0, 0.0, 0.585365853658...   
818  [0.4782608695652174, 0.08, 0.16666666666666666...   

                                            ROUGE_mean  \
0    [0.3106060606060606, 0.1904761904761905, 0.072...   
1    [0.09523809523809523, 0.0784313725490196, 0.08...   
..                                                 ...   
817  [0.45955882352941185, 0.0, 0.0, 0.561184073379...   
818  [0.3945981554677207, 0.05333333333333334, 0.12...   

                                         SBERT_s2a_sim  ...  \
0                   [0.6805704, 0.5117593, 0.84176743]  ...   
1    [0.6140934, 0.5550279, 0.49303842, 0.6147639, ...  ...   
..                                                 ...  ...   
817  [0.750149, 0.3195756, 0.17291635, 0.64767104, ...  ...   
818     [0.8827534, 0.32481486, 0.72412086, 0.6603297]  ...   

    TFIDF_SBERT_top60%_f1 SBERT_SBERT_top60%_f1 TFIDF_ROUGE_top80%_f1  \
0                0.500000              0.500000              0.500000   
1                0.769231              0.769231              0.882353   
..                    ...                   ...                   ...   
817              0.727273              0.909091              0.785714   
818              0.500000              1.000000              1.000000   

    SBERT_ROUGE_top80%_f1 TFIDF_SBERT_top80%_f1  SBERT_SBERT_top80%_f1  \
0             

In [ ]:
reddit_dataset = load_dataset('reddit', split='train[:5000]')
aeslc_dataset = load_dataset('aeslc', split='test')

Generating train split:   0%|          | 0/3848330 [00:00<?, ? examples/s]

Dataset reddit downloaded and prepared to /root/.cache/huggingface/datasets/reddit/default/1.0.0/98ba5abea674d3178f7588aa6518a5510dc0c6fa8176d9653a3546d5afcb3969. Subsequent calls will reuse this data.


Generating train split:   0%|          | 0/14436 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/1960 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/1906 [00:00<?, ? examples/s]

Dataset aeslc downloaded and prepared to /root/.cache/huggingface/datasets/aeslc/default/1.0.0/8d562772daa49c77ba4d77fbf90713819698774c172092c9aa9e7d3fb642d9ba. Subsequent calls will reuse this data.


In [ ]:
reddit_df = pd.DataFrame({"article": reddit_dataset['content'],"highlights": reddit_dataset['summary']})
reddit_df = tokenizer(reddit_df)
reddit_df = TFIDF_sim(reddit_df)
reddit_df = rouge_score(reddit_df)
reddit_df = SBERT_sim(reddit_df)
reddit_df = ranks(reddit_df)
reddit_df = compute_topKpct_f1_scores(reddit_df)
reddit_df

  0%|          | 0/5000 [00:00<?, ?it/s]

  0%|          | 0/5000 [00:00<?, ?it/s]

  0%|          | 0/5000 [00:00<?, ?it/s]

  0%|          | 0/5000 [00:00<?, ?it/s]

  0%|          | 0/5000 [00:00<?, ?it/s]

...

  0%|          | 0/5000 [00:00<?, ?it/s]

/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_classification.py:1609: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, "true nor predicted", "F-score is", len(true_sum))
/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_classification.py:1609: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, "true nor predicted", "F-score is", len(true_sum))
/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_classification.py:1609: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, "true nor predicted", "F-score is", len(true_sum))
/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_cl

  0%|          | 0/5000 [00:00<?, ?it/s]

/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_classification.py:1609: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, "true nor predicted", "F-score is", len(true_sum))
/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_classification.py:1609: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, "true nor predicted", "F-score is", len(true_sum))
/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_classification.py:1609: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, "true nor predicted", "F-score is", len(true_sum))
/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_cl

article  \
0     I think it should be fixed on either UTC stand...   
1     Art is about the hardest thing to categorize i...   
...                                                 ...   
4998  Intel recommends not going over 1,5V with the ...   
4999  I think there are two sides to every story and...   

                                             highlights  \
0         Shifting seasonal time is no longer worth it.   
1                            Personal opinions 'n shit.   
...                                                 ...   
4998  You can do it, but this RAM is not ideal anyways.   
4999  I honestly don't know what to think because we...   

                                              sentences  \
0     [I think it should be fixed on either UTC stan...   
1     [Art is about the hardest thing to categorize ...   
...                                                 ...   
4998  [Intel recommends not going over 1,5V with the...   
4999  [I think there are two sides to every story an...   

                                              TFIDF_sim  \
0     [0.3333920265515471, 0.6164165867450068, 0.649...   
1     [0.37296152652515974, 0.33668143043359144, 0.3...   
...                                                 ...   
4998           [0.7849919401597454, 0.7351613073640042]   
4999  [0.32151118869953615, 0.6348498772881802, 0.43...   

                                              raw_ROUGE  \
0     [{'rouge1': (0.05, 0.125, 0.07142857142857144)...   
1     [{'rouge1': (0.0, 0.0, 0.0), 'rouge2': (0.0, 0...   
...                                                 ...   
4998  [{'rouge1': (0.11538461538461539, 0.2727272727...   
4999  [{'rouge1': (0.35294117647058826, 0.1153846153...   

                                                     R1  \
0     [0.07142857142857144, 0.12, 0.0357142857142857...   
1        [0.0, 0.10526315789473685, 0.0, 0.0, 0.0, 0.0]   
...                                                 ...   
4998         [0.16216216216216214, 0.30769230769230765]   
4999  [0.1739130434782609, 0.0, 0.08823529411764705,...   

                                                   R2  \
0                           [0.0, 0.0, 0.0, 0.0, 0.0]   
1                      [0.0, 0.0, 0.0, 0.0, 0.0, 0.0]   
...                                               ...   
4998                                       [0.0, 0.0]   
4999  [0.0, 0.0, 0.0, 0.024096385542168676, 0.0, 0.0]   

                                                     RL  \
0     [0.07142857142857144, 0.08, 0.0357142857142857...   
1        [0.0, 0.10526315789473685, 0.0, 0.0, 0.0, 0.0]   
...                                                 ...   
4998         [0.10810810810810811, 0.15384615384615383]   
4999  [0.11594202898550726, 0.0, 0.05882352941176470...   

                                             ROUGE_mean  \
0     [0.04761904761904762, 0.06666666666666667, 0.0...   
1        [0.0, 0.07017543859649124, 0.0, 0.0, 0.0, 0.0]   
...                                                 ...   
4998          [0.0900900900900901, 0.15384615384615383]   
4999  [0.09661835748792273, 0.0, 0.04901960784313725...   

                                          SBERT_s2a_sim  ...  \
0     [0.3952682, 0.7601219, 0.7317569, 0.70088553, ...  ...   
1     [0.613292, 0.6864121, 0.24308132, 0.80403364, ...  ...   
...                                                 ...  ...   
4998                           [0.94798815, 0.61890435]  ...   
4999  [0.5453534, 0.6021873, 0.54970026, 0.55294436,...  ...   

     TFIDF_SBERT_top60%_f1 SBERT_SBERT_top60%_f1 TFIDF_ROUGE_top80%_f1  \
0                 0.666667              0.666667                  0.75   
1                 0.500000              0.750000                  0.80   
...                    ...                   ...                   ...   
4998              0.000000              0.000000                  0.00   
4999              0.500000              0.500000                  0.80   

     SBERT_ROUGE_top80%_f1 TFIDF_SB

In [ ]:
aeslc_df = pd.DataFrame({"article": aeslc_dataset['email_body'],"highlights": aeslc_dataset['subject_line']})
aeslc_df = tokenizer(aeslc_df)
aeslc_df = TFIDF_sim(aeslc_df)
aeslc_df = rouge_score(aeslc_df)
aeslc_df = SBERT_sim(aeslc_df)
aeslc_df = ranks(aeslc_df)
aeslc_df = compute_topKpct_f1_scores(aeslc_df)
aeslc_df

  0%|          | 0/1906 [00:00<?, ?it/s]

  0%|          | 0/1906 [00:00<?, ?it/s]

  0%|          | 0/1906 [00:00<?, ?it/s]

  0%|          | 0/1906 [00:00<?, ?it/s]

  0%|          | 0/1906 [00:00<?, ?it/s]

...

  0%|          | 0/1906 [00:00<?, ?it/s]

/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_classification.py:1609: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, "true nor predicted", "F-score is", len(true_sum))


  0%|          | 0/1906 [00:00<?, ?it/s]

/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_classification.py:1609: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, "true nor predicted", "F-score is", len(true_sum))


article  \
0     Phillip,   Could you please do me a favor?\nI ...   
1     The following reports have been waiting for yo...   
...                                                 ...   
1904  Please find attached the latest, and what shou...   
1905  John,  Further to our conversation last week, ...   

                                    highlights  \
0                           Huntley/question\n   
1     Expense Reports Awaiting Your Approval\n   
...                                        ...   
1904                   Latest Marketing List\n   
1905                              Power Pool\n   

                                              sentences  \
0     [Phillip,   Could you please do me a favor?, \...   
1     [The following reports have been waiting for y...   
...                                                 ...   
1904  [Please find attached the latest, and what sho...   
1905  [John,  Further to our conversation last week,...   

                                              TFIDF_sim  \
0     [0.35163508525338616, 0.4991050926945032, 0.42...   
1     [0.5407859885920497, 0.15847747106292678, 0.80...   
...                                                 ...   
1904  [0.3353522607517956, 0.4073458497633405, 0.355...   
1905  [0.44516745218847664, 0.10101332105168959, 0.9...   

                                              raw_ROUGE  \
0     [{'rouge1': (0.0, 0.0, 0.0), 'rouge2': (0.0, 0...   
1     [{'rouge1': (0.21428571428571427, 0.6, 0.31578...   
...                                                 ...   
1904  [{'rouge1': (0.13636363636363635, 1.0, 0.24000...   
1905  [{'rouge1': (0.045454545454545456, 1.0, 0.0869...   

                                                     R1  \
0                        [0.0, 0.0, 0.0, 0.0, 0.0, 0.0]   
1                   [0.3157894736842105, 0.0, 0.0, 0.0]   
...                                                 ...   
1904  [0.24000000000000002, 0.08695652173913045, 0.0...   
1905               [0.08695652173913045, 0.0, 0.0, 0.0]   

                                                     R2  \
0                        [0.0, 0.0, 0.0, 0.0, 0.0, 0.0]   
1                  [0.11764705882352941, 0.0, 0.0, 0.0]   
...                                                 ...   
1904  [0.08695652173913042, 0.0, 0.0, 0.0, 0.0, 0.0,...   
1905               [0.04545454545454545, 0.0, 0.0, 0.0]   

                                                     RL  \
0                        [0.0, 0.0, 0.0, 0.0, 0.0, 0.0]   
1                   [0.3157894736842105, 0.0, 0.0, 0.0]   
...                                                 ...   
1904  [0.24000000000000002, 0.08695652173913045, 0.0...   
1905               [0.08695652173913045, 0.0, 0.0, 0.0]   

                                             ROUGE_mean  \
0                        [0.0, 0.0, 0.0, 0.0, 0.0, 0.0]   
1                  [0.24974200206398348, 0.0, 0.0, 0.0]   
...                                                 ...   
1904  [0.18898550724637683, 0.05797101449275363, 0.0...   
1905               [0.07312252964426878, 0.0, 0.0, 0.0]   

                                          SBERT_s2a_sim  ...  \
0     [0.19079478, 0.77448183, 0.60582685, 0.5782458...  ...   
1         [0.7259392, 0.29196727, 0.7673269, 0.2607701]  ...   
...                                                 ...  ...   
1904  [0.38120782, 0.38050288, 0.2297441, 0.49543896...  ...   
1905     [0.85615695, 0.3747284, 0.6992566, 0.08441313]  ...   

     TFIDF_SBERT_top60%_f1 SBERT_SBERT_top60%_f1 TFIDF_ROUGE_top80%_f1  \
0                 0.500000              0.500000              0.800000   
1                 1.000000              1.000000              1.000000   
...                    ...                   ...                   ...   
1904              0.714286              0.428571              0.666667   
1905              1.000000              1.000000              0.666667   

     SBERT_ROUGE_top80%_f1 TFIDF_SBERT_top80%_f1  SBERT_SBERT_top80%_f1  \
0 

In [ ]:
import pandas as pd
from google.colab import drive
#cnn_dailymail_df.to_pickle('cnn_dailymail.dfpkl')
SAMsum_df.to_pickle('SAMsum.dfpkl')
reddit_df.to_pickle('reddit.dfpkl')
aeslc_df.to_pickle('aeslc.dfpkl')


In [ ]:
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!mkdir -p /content/gdrive/MyDrive/
#!cp cnn_dailymail.dfpkl /content/gdrive/MyDrive/cnn_dailymail.dfpkl
!cp SAMsum.dfpkl /content/gdrive/MyDrive/SAMsum.dfpkl
!cp reddit.dfpkl /content/gdrive/MyDrive/reddit.dfpkl
!cp aeslc.dfpkl /content/gdrive/MyDrive/aeslc.dfpkl

In [ ]:
#path = '/content/drive/My Drive/cnn_dailymail.csv'
#with open(path, 'w', encoding = 'utf-8-sig') as f:
#  cnn_dailymail_df.to_csv(f)
path = '/content/drive/My Drive/SAMsum.csv'
with open(path, 'w', encoding = 'utf-8-sig') as f:
  SAMsum_df.to_csv(f)
path = '/content/drive/My Drive/reddit.csv'
with open(path, 'w', encoding = 'utf-8-sig') as f:
  reddit_df.to_csv(f)
path = '/content/drive/My Drive/aeslc.csv'
with open(path, 'w', encoding = 'utf-8-sig') as f:
  aeslc_df.to_csv(f) 

In [ ]:
!wget -O cnn_dailymail.dfpkl https://uoguelphca-my.sharepoint.com/:u:/g/personal/chungyan_uoguelph_ca/EetFsM17mc5Hje7JZAmUTJcBiABnzB0V_ZpvhVcXJq2SYA?download=1
df = pd.read_pickle('exp9.230306.0024.dfpkl')